## horseIDとjockeyIDの取得

In [106]:
import pandas as pd
import requests
from bs4 import BeautifulSoup
import pandas as pd
import re
import time
from tqdm import tqdm

pd.options.display.max_rows = 5
pd.options.display.max_columns = 100
pd.options.display.max_colwidth = 30

In [62]:

df = pd.read_pickle('inner_df.pickle')
race_id_list = df.index.unique()
type(race_id_list[0])
# race_id_list = ["202101010101","202101010102"]

str

In [63]:
test = {}
def scrape_race_results(race_id_lists,par_race_results={}):
  race_results = par_race_results
  for _race_id in tqdm(race_id_lists):
    # if _race_id in race_result.keys():
    #   continue
    time.sleep(1)
    try:
      # スクレイピング
      url = "https://race.netkeiba.com/race/result.html?race_id=" + _race_id
      html = requests.get(url)
      html.encoding= "EUC_JP"
      soup = BeautifulSoup(html.text, "html.parser")
      
      # horse_id
      horse_id_list = []      
      horse_a_list = soup.find('table',attrs={"summary":"全着順"}).find_all('a',attrs={"href":re.compile("/horse/")})
      for a in horse_a_list:
        horse_id = re.findall(r'\d+',a["href"])
        horse_id_list.append(horse_id[0])
      Series1 = pd.Series(data = horse_id_list,dtype=str,name="horse_id")
      # jockey_id
      jockey_id_list = []
      jockey_a_list = soup.find('table',attrs={"summary":"全着順"}).find_all('a',attrs={"href":re.compile("/jockey/")})
      for u in jockey_a_list:
        jockey_id = re.findall(r'\d+',u["href"])
        jockey_id_list.append(jockey_id[0])
      Series2 = pd.Series(data = jockey_id_list,dtype=str,name="jockey_id")
      
      results = pd.concat([Series1, Series2], axis=1)
      test[_race_id] = results
      
    except UnicodeDecodeError as e:
      # print(e)
      # print(f"レースID: {race_id} のデータはありません")
      continue
    except KeyboardInterrupt:
      break
    except TimeoutError:
      break
  return test

In [64]:
results_new = scrape_race_results(race_id_list)
results_new

100%|██████████| 24/24 [00:32<00:00,  1.33s/it]


{'202102010101':      horse_id jockey_id
 0   201910...     01182
 1   201910...     01093
 ..        ...       ...
 8   201910...     01177
 9   201910...     01112
 
 [10 rows x 2 columns],
 '202102010102':      horse_id jockey_id
 0   201810...     01030
 1   201810...     01181
 ..        ...       ...
 10  201810...     01144
 11  201810...     01015
 
 [12 rows x 2 columns],
 '202102010103':      horse_id jockey_id
 0   201810...     01095
 1   201810...     01182
 ..        ...       ...
 10  201810...     01185
 11  201810...     01170
 
 [12 rows x 2 columns],
 '202102010104':      horse_id jockey_id
 0   201810...     01144
 1   201810...     01185
 ..        ...       ...
 10  201810...     01182
 11  201810...     01181
 
 [12 rows x 2 columns],
 '202102010105':      horse_id jockey_id
 0   201910...     01156
 1   201910...     05339
 ..        ...       ...
 8   201910...     01181
 9   201910...     01161
 
 [10 rows x 2 columns],
 '202102010106':      horse_id jockey_id

In [65]:
for key in results_new.keys():
  results_new[key].index = [key] * len(results_new[key])
results = pd.concat([results_new[key] for key in results_new.keys()],sort=False)

In [66]:
print(type(results))
print(len(results))
print(type(df))
print(len(df))

<class 'pandas.core.frame.DataFrame'>
313
<class 'pandas.core.frame.DataFrame'>
313


In [67]:
# pd.set_option('display.max_rows',None)

df_add_id = pd.concat([df,results],axis=1)

In [68]:
df_add_id

着順  枠  馬番       馬名  性齢    斤量    騎手     タイム     着差  人気  単勝オッズ  \
2021020...   1  4   4  ナムラリコリス  牝2  52.0   △泉谷  1:09.3    NaN   1    1.4   
2021020...   2  1   1     プラソン  牝2  54.0   藤岡佑  1:09.4    1/2   2    5.5   
...         .. ..  ..      ...  ..   ...   ...     ...    ...  ..    ...   
2021030...  15  7  14   トランザクト  牡3  52.0  ◇藤田菜  1:10.6  1.3/4   5   14.8   
2021030...  16  4   8       リゼ  牝5  55.0    石川  1:12.4      大  14  107.5   

             後3F コーナー通過順     厩舎  馬体重(増減)       date race_type course_ren  \
2021020...  35.7     2-2   栗東大橋  466(+2)  2021年7月3日         芝       1200   
2021020...  35.9     1-1   栗東寺島  430(+2)  2021年7月3日         芝       1200   
...          ...     ...    ...      ...        ...       ...        ...   
2021030...  39.3     4-7   美浦武藤  496(-4)  2021年7月3日         ダ       1150   
2021030...  39.5   15-15  美浦田中清  446(-4)  2021年7月3日         ダ       1150   

           weather ground_state   horse_id jockey_id  
2021020...       晴          良    201910...     01182  
2021020...       晴          良    201910...     01093  
...            ...        ...          ...       ...  
2021030...       曇          稍    201810...     01164  
2021030...       曇          稍    201610...     01150  

[313 rows x 22 columns]

In [69]:
df_add_id.to_pickle("df_add_id.pickle")

----

## idのリストを作成

In [70]:
horse_id_list = df_add_id["horse_id"].unique()
len(horse_id_list)
# horse_id_list = horse_id_list
# horse_id_list = ['2018105875', '2018105258', '2018101134', '2018102791']

313

In [71]:
# url = "https://db.netkeiba.com/horse/2019109094"
# url = "https://db.netkeiba.com/horse/2018102444"
# time.sleep(1)
# pd.read_html(url,match='日付')

In [72]:
test = {}
def scrape_horse_results(horse_id_list,par_horse_results={}):
  horse_results = par_horse_results
  for _horse_id in tqdm(horse_id_list):
    # if _horse_id in horse_id_list.keys():
    #   continue
    time.sleep(2)
    try:
      # スクレイピング
      url = "https://db.netkeiba.com/horse/" + _horse_id
      time.sleep(1)
      # [0]をつけてリストの中だけを取得
      horse_results[_horse_id] = pd.read_html(url,match='日付')[0]
      
    except UnicodeDecodeError as e:
      # print(e)
      # print(f"レースID: {race_id} のデータはありません")
      continue
    except KeyboardInterrupt:
      break
        
    except TimeoutError:
      break
    # print(horse_results)
      
  return horse_results

In [73]:
horse_results = scrape_horse_results(horse_id_list)

100%|██████████| 313/313 [17:53<00:00,  3.43s/it]


In [74]:
horse_results

{'2019102534':            日付    開催 天気   R       レース名  映像  頭数  枠番  馬番    オッズ  人気  着順    騎手  \
 0   2022/0...  2中京3  曇  11  中スポ賞ファ... NaN  18   4   7  141.9  16  18  泉谷楓真   
 1   2022/0...  1中京5  晴  10     紅梅S(L) NaN   9   4   4   15.2   5   6  泉谷楓真   
 ..        ...   ... ..  ..        ...  ..  ..  ..  ..    ...  ..  ..   ...   
 4   2021/0...  1函館1  晴   1      2歳未勝利 NaN  10   4   4    1.4   1   1  泉谷楓真   
 5   2021/0...  1札幌3  曇   5       2歳新馬 NaN  12   8  11   15.7   8   2  泉谷楓真   
 
     斤量     距離 馬場 馬場指数     タイム   着差 ﾀｲﾑ指数   通過        ペース    上り       馬体重  \
 0   55  芝1400  稍   **  1:23.7  2.8    **  2-2  33.1-36.5  39.1  462(-12)   
 1   55  芝1400  良   **  1:22.5  0.7    **  3-2  34.9-35.3  35.8   474(-2)   
 ..  ..    ... ..  ...     ...  ...   ...  ...        ...   ...       ...   
 4   52  芝1200  良   **  1:09.3 -0.1    **  2-2  33.5-35.8  35.7   466(+2)   
 5   52  芝1200  良   **  1:08.5  0.6    **  4-2  33.6-34.3  34.3    464(0)   
 
     厩舎ｺﾒﾝﾄ  備考  勝ち馬(2着馬)     賞金  
 0      NaN

In [75]:
for key in horse_results.keys():
  horse_results[key].index = [key] * len(horse_results[key])
results = pd.concat([horse_results[key] for key in horse_results.keys()],sort=False)

In [76]:
# results

In [77]:
results.to_csv("horse_vs_data.csv")

In [134]:
pd.set_option('display.max_rows',None)

df = pd.read_csv('horse_vs_data.csv')
df = df.iloc[:,:29]

/var/folders/g6/k526pb596zv_zcdn87rsfwqc0000gn/T/ipykernel_40322/1182967401.py:3: DtypeWarning: Columns (14,28,45,46,47,48,49,50,51,52,53,54,55,56,57,58,59,109,110) have mixed types. Specify dtype option on import or set low_memory=False.
  df = pd.read_csv('horse_vs_data.csv')


In [135]:
df.columns


Index(['日付', '開催', '天気', 'R', 'レース名', '映像', '頭数', '枠番', '馬番', 'オッズ', '人気',
       '着順', '騎手', '斤量', '距離', '馬場', '馬場指数', 'タイム', '着差', 'ﾀｲﾑ指数', '通過', 'ペース',
       '上り', '馬体重', '厩舎ｺﾒﾝﾄ', '備考', '勝ち馬(2着馬)', '賞金', '騎手金'],
      dtype='object')

In [136]:
print(df["日付"].value_counts())
print(df["開催"].value_counts())
print(df["天気"].value_counts())
print(df["R"].value_counts())
print(df["レース名"].value_counts())
print(df["映像"].value_counts())
print(df["頭数"].value_counts())
print(df["枠番"].value_counts())
print(df["馬番"].value_counts())
print(df["オッズ"].value_counts())
print(df["人気"].value_counts())
print(df["着順"].value_counts())
print(df["騎手"].value_counts())
print(df["斤量"].value_counts())

2021/07/03    304
2021/07/17     42
2021/07/18     34
2021/09/04     34
2021/06/20     27
2021/05/01     26
2021/11/07     25
2021/02/28     24
2021/07/31     24
2021/11/21     24
2021/08/29     24
2021/02/06     24
2021/06/19     24
2021/07/24     24
2021/11/06     23
2020/09/05     23
2021/08/22     23
2020/12/05     23
2021/11/20     23
2021/10/10     22
2022/03/27     22
2021/02/27     22
2021/06/12     22
2021/01/23     22
2021/04/11     22
2021/05/15     21
2021/03/13     21
2021/01/31     20
2021/08/08     19
2021/05/16     19
2021/05/23     19
2021/04/10     19
2021/08/01     19
2021/08/15     19
2020/11/14     19
2022/02/26     19
2021/08/28     19
2021/07/25     18
2021/08/21     18
2020/07/11     18
2021/10/24     18
2021/09/25     18
2021/03/28     18
2021/06/13     18
2021/12/05     18
2020/07/19     18
2020/12/06     18
2020/11/01     18
2021/02/13     17
2021/04/25     17
2020/12/13     17
2021/02/21     17
2021/05/09     17
2021/12/12     17
2021/01/16     17
2020/10/17

In [138]:
df


日付     開催   天気     R                レース名  映像    頭数   枠番  \
2019102534  2022/03/19   2中京3    曇  11.0      中スポ賞ファルコンS(G3) NaN  18.0  4.0   
2019102534  2022/01/15   1中京5    晴  10.0              紅梅S(L) NaN   9.0  4.0   
2019102534  2021/12/12   6阪神4    晴  11.0       阪神ジュベナイルF(G1) NaN  18.0  1.0   
2019102534  2021/07/17   1函館5    晴  11.0           函館2歳S(G3) NaN  11.0  8.0   
2019102534  2021/07/03   1函館1    晴   1.0               2歳未勝利 NaN  10.0  4.0   
2019102534  2021/06/19   1札幌3    曇   5.0                2歳新馬 NaN  12.0  8.0   
2019105130  2022/03/20  1阪神12    晴   6.0             3歳1勝クラス NaN   9.0  7.0   
2019105130  2022/02/05   1東京3    曇   9.0          春菜賞(1勝クラス) NaN  16.0  1.0   
2019105130  2021/12/05   6阪神2    曇   9.0        さざんか賞(1勝クラス) NaN   8.0  8.0   
2019105130  2021/11/21   5阪神6    晴   9.0         秋明菊賞(1勝クラス) NaN  11.0  1.0   
2019105130  2021/10/02   5中京8    晴   9.0           ききょうS(OP) NaN   7.0  6.0   
2019105130  2021/09/04   2札幌7    晴   1.0               2歳未勝利 NaN   9.0  8.0   
2019105130  2021/08/15   2札幌2    曇   1.0               2歳未勝利 NaN   9.0  5.0   
2019105130  2021/07/03   1函館1    晴   1.0               2歳未勝利 NaN  10.0  1.0   
2019105130  2021/06/12   1札幌1    曇   5.0                2歳新馬 NaN  12.0  4.0   
2019100936  2022/02/05   1東京3    曇   9.0          春菜賞(1勝クラス) NaN  16.0  6.0   
2019100936  2022/01/15   1中山5    晴   9.0         菜の花賞(1勝クラス) NaN  11.0  7.0   
2019100936  2021/12/12   6中京4    曇  10.0        つわぶき賞(1勝クラス) NaN  12.0  6.0   
2019100936  2021/11/21   5東京6    曇   9.0          赤松賞(1勝クラス) NaN   9.0  2.0   
2019100936  2021/09/05   2札幌8    晴  10.0           すずらん賞(OP) NaN   9.0  3.0   
2019100936  2021/07/25   1函館8    曇   1.0               2歳未勝利 NaN   7.0  1.0   
2019100936  2021/07/03   1函館1    晴   1.0               2歳未勝利 NaN  10.0  8.0   
2019100936  2021/06/19   1札幌3    曇   5.0                2歳新馬 NaN  12.0  5.0   
2019100052  2022/03/21   2中京4    晴   4.0               3歳未勝利 NaN  16.0  1.0   
2019100052  2022/02/26   2中山1    晴   5.0               3歳未勝利 NaN  16.0  7.0   
2019100052  2021/11/21   2福島6    晴   1.0               2歳未勝利 NaN  16.0  5.0   
2019100052  2021/10/30   5新潟7    晴   3.0               2歳未勝利 NaN  15.0  8.0   
2019100052  2021/10/10   5新潟2    晴   1.0               2歳未勝利 NaN  15.0  3.0   
2019100052  2021/08/01  1函館10    曇   1.0               2歳未勝利 NaN   9.0  8.0   
2019100052  2021/07/03   1函館1    晴   1.0               2歳未勝利 NaN  10.0  3.0   
2019100052  2021/06/19   1札幌3    曇   5.0                2歳新馬 NaN  12.0  6.0   
2019104841  2022/03/26   2阪神1   小雨   1.0               3歳未勝利 NaN  16.0  7.0   
2019104841  2021/09/04   2札幌7    晴   1.0               2歳未勝利 NaN   9.0  2.0   
2019104841  2021/08/15   2札幌2    曇   1.0               2歳未勝利 NaN   9.0  3.0   
2019104841  2021/07/03   1函館1    晴   1.0               2歳未勝利 NaN  10.0  5.0   
2019104841  2021/06/26   1札幌5    晴   5.0                2歳新馬 NaN   8.0  1.0   
2019105332  2022/03/27   3中山2    晴   1.0               3歳未勝利 NaN  16.0  1.0   
2019105332  2022/01/30   1東京2    晴   3.0               3歳未勝利 NaN  16.0  4.0   
2019105332  2022/01/05   1中山1    晴   2.0               3歳未勝利 NaN  16.0  5.0   
2019105332  2021/07/03   1函館1    晴   1.0               2歳未勝利 NaN  10.0  2.0   
2019105332  2021/06/20   1札幌4    曇   5.0                2歳新馬 NaN  16.0  6.0   
2019103404  2022/03/09    名古屋    晴   2.0                3歳4組 NaN  10.0  3.0   
2019103404  2022/02/16    名古屋    晴   3.0                3歳5組 NaN  11.0  3.0   
2019103404  2022/02/02    名古屋    晴   1.0                3歳4組 NaN  11.0  8.0   
2019103404  2021/12/30     水沢    曇   2.0              2歳C2一組 NaN   7.0  6.0   
2019103404  2021/12/21     水沢  NaN   1.0              2歳C2三組 NaN   0.0  3.0   
2019103404  2021/12/07     水沢    曇   1.0              2歳C2二組 NaN   9.0  1.0   
2019103404  2021/11/07   2福島2    晴   2.0               2歳未勝利 NaN  16.0  1.0   
2019103404  2021/09/18   4中山3    雨   3.0               2歳未勝利 NaN  16.0  2.0   
2019103404  2021/08/22   2札幌4    晴   1.0               2歳未勝利 NaN  13.0